## Shell Contact Example

In [1]:
# !pip install debugpy

In [ ]:
import numpy as np

import dismech


geom = dismech.GeomParams(rod_r0=0.005,
                          shell_h=0.001)

material = dismech.Material(density=2000,
                            youngs_rod=0,
                            youngs_shell=2e10,
                            poisson_rod=0,
                            poisson_shell=0.5)

shell_contact_sim = dismech.SimParams(static_sim=False,
                                  two_d_sim=False,   # no twisting
                                  use_mid_edge=False,
                                  use_line_search=True,
                                  show_floor=False,
                                  log_data=True,
                                  log_step=1,
                                  dt=5e-4,
                                  max_iter=120,
                                  total_time=0.6,
                                  plot_step=1,
                                  tol=1e-4,
                                  ftol=1e-4,
                                  dtol=1e-2)

env = dismech.Environment()
env.add_force('gravity', g=np.array([0.0, 0.0, -9.81]))
# env.add_force('floorContact', ground_z=-1e-3, stiffness=20, delta=1e-4, h=1e-3)
env.add_force('selfContact', delta=1e-4, h=1e-3, kc=10)
env.add_force('damping', eta = 0.1)
#env.set_static()   

# geo = dismech.Geometry.from_txt('2random_mesh_20.txt')
geo = dismech.Geometry.from_txt('2random_mesh_8.txt')
# geo = dismech.Geometry.from_txt('input_shell_more_curved_scaled.txt')

robot = dismech.SoftRobot(geom, material, geo, shell_contact_sim, env)

# fixed_points = np.array(np.where(
#     (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 0] <= 0.01) &
#     (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 2] == 0.0)
# )[0])
fixed_points = np.array(np.where(
    (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 2] < 0.001) # (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 2] < 0.001)
)[0])

# fixed_points = np.array(np.where(
#     (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 0] <= 0.455) & 
#     (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 0] >= 0.445) # (robot.state.q[:robot.end_node_dof_index].reshape(-1, 3)[:, 2] < 0.001)
# )[0])


robot = robot.fix_nodes(fixed_points)

# u = robot.state.u
# u[11] = -0.5
# u[14] = -0.5
# u[17] = -0.5

### Time Stepping

As we are performing a static simulation, we must change gravity for each time step.

In [3]:
stepper = dismech.ImplicitEulerTimeStepper(robot)

robots = stepper.simulate()

qs = np.stack([robot.state.q for robot in robots])

delta: 0.1
h: 1.0
K1: 150.0
scale:  1000.0
kc:  10
upper limit for quadratic: 1.9
upper limit for smooth: 2.1
0.8123700660956824
current_time:  0.0005
1.6223041411392936
current_time:  0.001
2.4297922723822625
2.0780488379878076e-06
current_time:  0.0015
3.2347966065660954
5.40252852044023e-06
current_time:  0.002
4.037277066536917
1.133999247383654e-05
current_time:  0.0025
4.83719535443535
2.07201960587322e-05
current_time:  0.003
5.63451786554059
3.4388184234297004e-05
current_time:  0.0035
6.429217684123753
5.31983254117106e-05
current_time:  0.004
7.221275593932978
7.802634653232058e-05
current_time:  0.0045000000000000005
8.010680150908625
0.00010976909665445477
current_time:  0.005
8.797426977663022
0.00014928437006091888
current_time:  0.0055
9.581517490201307
0.00019735623454044998
current_time:  0.006
10.3629573033861
0.0002546517231451075
current_time:  0.006500000000000001
11.141754549329194
0.0003216709361730768
current_time:  0.007
11.917918320569962
0.0003987540326332767

In [4]:
t = np.arange(robot.sim_params.total_time, step=robot.sim_params.dt)
options = dismech.AnimationOptions(title='Shell contact p2p', plot_step=10)

fig = dismech.get_interactive_animation_plotly(robot, t, qs, options)
fig.show()

In [5]:
# ani = dismech.get_animation(robot, t, qs, options)
# ani.save('5e-5.gif')